In [17]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.linear_model import LinearRegression
from tqdm import tqdm

# data

In [18]:
DAY = 0

In [19]:
df = pd.read_csv(f"./round-3-island-data-bottle/prices_round_3_day_{DAY}.csv", sep=";", header=0)

In [20]:
def swmid(row):
    bid = row['bid_price_1']
    ask = row['ask_price_1']
    bid_volume = row['bid_volume_1']
    ask_volume = row['ask_volume_1']
    return ((bid*ask_volume + ask*bid_volume)/(bid_volume + ask_volume))

def mm_mid_basket(row, volume_cutoff=10):
    # Find the best bid with volume >= volume_cutoff
    for i in range(1, 4):
        if row[f'bid_volume_{i}'] >= volume_cutoff:
            best_bid = row[f'bid_price_{i}']
            break
    else:
        # No bid with sufficient volume found
        best_bid = None

    # Find the best ask with volume >= volume_cutoff
    for i in range(1, 4):
        if row[f'ask_volume_{i}'] >= volume_cutoff:
            best_ask = row[f'ask_price_{i}']
            break
    else:
        # No ask with sufficient volume found
        best_ask = None

    # Calculate the mid-price if both best bid and best ask are found
    if best_bid is not None and best_ask is not None:
        mid_price = (best_bid + best_ask) / 2
        return mid_price
    else:
        # Return the mid_price column value as default
        return row['mid_price']
    

In [21]:
def fair_price(row):
    if row['product'] == 'GIFT_BASKET':
        return mm_mid_basket(row, volume_cutoff=10)
    else:
        return swmid(row)

df['fair'] = df.apply(fair_price, axis=1)

In [22]:
# Define the weights dictionary
weights = {
    'CHOCOLATE': 4,
    'STRAWBERRIES': 6,
    'ROSES': 1
}

# Get the unique product names
products = df['product'].unique()

# Create a new dataframe 'df_fairs' with the desired columns
columns = ['timestamp'] + list(products) + ['SYNTHETIC']
df_fairs = pd.DataFrame(columns=columns)

# Iterate over unique timestamps in the original dataframe
for timestamp in df['timestamp'].unique():
    # Get the rows for the current timestamp
    rows = df[df['timestamp'] == timestamp]
    
    # Create a dictionary to store the fair values for each product
    fairs = {}
    
    # Iterate over each product and extract its fair value
    for product in products:
        fair = rows.loc[rows['product'] == product, 'fair'].values[0]
        fairs[product] = fair
    
    # Calculate the synthetic fair
    synthetic_fair = sum(fairs[product] * weights.get(product, 0) for product in ['CHOCOLATE', 'STRAWBERRIES', 'ROSES'])
    
    # Create a new row as a DataFrame
    new_row = pd.DataFrame({'timestamp': [timestamp], **{product: [fairs[product]] for product in products}, 'SYNTHETIC': [synthetic_fair]})
    
    # Concatenate the new row with df_fairs
    df_fairs = pd.concat([df_fairs, new_row], ignore_index=True)

# Reset the index of df_fairs (optional)
df_fairs = df_fairs.reset_index(drop=True)

/var/folders/qd/7_02v1xx1nx_p2rj9mxjqzzh0000gn/T/ipykernel_47070/630176225.py:35: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [23]:
df_fairs

timestamp    CHOCOLATE  STRAWBERRIES         ROSES  GIFT_BASKET  \
0            0  8000.000000   4000.000000  15000.000000      71355.0   
1          100  8001.261307   3999.500000  15000.000000      71349.5   
2          200  8001.000000   3999.500000  15000.743902      71344.5   
3          300  8002.255814   3999.500000  15000.000000      71350.0   
4          400  8002.000000   3999.227011  14997.500000      71341.5   
...        ...          ...           ...           ...          ...   
9995    999500  7987.310881   4031.000000  14543.231707      71141.5   
9996    999600  7988.708571   4031.000000  14548.000000      71137.5   
9997    999700  7987.718750   4031.000000  14546.277108      71128.5   
9998    999800  7989.500000   4031.000000  14546.755814      71138.0   
9999    999900  7988.000000   4030.693182  14550.219512      71123.0   

         SYNTHETIC  
0     71000.000000  
1     71002.045226  
2     71001.743902  
3     71006.023256  
4     71000.862069  
...            ...  
9995  70678.475231  
9996  70688.834286  
9997  70683.152108  
9998  70690.755814  
9999  70686.378603  

[10000 rows x 6 columns]

## boellinger band

UFCK fuck fuck fuck fuci kuf ckf uckf cu fk 

In [24]:
df_fairs = df_fairs[['timestamp', "CHOCOLATE", "STRAWBERRIES", "ROSES", "GIFT_BASKET", 'SYNTHETIC']]

In [25]:
df_fairs['BASKET_MINUS_SYNTHETIC'] = df_fairs['GIFT_BASKET'] - df_fairs["SYNTHETIC"]

In [62]:
import pandas as pd
import plotly.graph_objects as go

def bollinger_bands(data, column='BASKET_MINUS_SYNTHETIC', window=20, num_std=2):
    """
    Calculate Bollinger Bands for a given DataFrame and column.
    
    Parameters:
    data (pd.DataFrame): The input DataFrame.
    column (str): The name of the column to calculate Bollinger Bands for.
    window (int): The rolling window size for the Simple Moving Average (SMA).
    num_std (int): The number of standard deviations for the upper and lower bands.
    
    Returns:
    pd.DataFrame: The input DataFrame with additional columns for the Bollinger Bands.
    """
    # Calculate the Simple Moving Average (SMA)
    data['SMA'] = data[column].rolling(window=window).mean()
    
    # Calculate the standard deviation
    data['STD'] = data[column].rolling(window=window).std()
    
    # Calculate the upper and lower Bollinger Bands
    data['UPPER_BAND'] = data['SMA'] + (data['STD'] * num_std)
    data['LOWER_BAND'] = data['SMA'] - (data['STD'] * num_std)
    
    return data

# Example usage
df_fairs = bollinger_bands(df_fairs, window=200, num_std=1.5)

# Calculate the change in STD
df_fairs['STD_CHANGE'] = df_fairs['STD'].diff()

# Create the plot
fig = go.Figure()

# Add the BASKET_MINUS_SYNTHETIC line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['BASKET_MINUS_SYNTHETIC'].ewm(halflife=5).mean(),
                         mode='lines', name='BASKET_MINUS_SYNTHETIC'))

# Add the Upper Bollinger Band line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['UPPER_BAND'],
                         mode='lines', name='Upper Band', line=dict(color='red')))

# Add the Simple Moving Average (SMA) line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['SMA'],
                         mode='lines', name='SMA', line=dict(color='blue')))

# Add the Lower Bollinger Band line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['LOWER_BAND'],
                         mode='lines', name='Lower Band', line=dict(color='green')))

# Add the change in STD line on a separate y-axis
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['STD'],
                         mode='lines', name='STD', line=dict(color='purple'),
                         yaxis='y2'))

# Update the layout to include the secondary y-axis
fig.update_layout(
    title='Bollinger Bands with STD',
    xaxis_title='Timestamp',
    yaxis=dict(title='BASKET_MINUS_SYNTHETIC'),
    yaxis2=dict(title='STD', overlaying='y', side='right')
)

# Display the plot
fig.show()

In [53]:
def identify_regime(data, mean=370, lookback=20, ewma=0):
    """
    Identify the regime based on the price's interaction with Bollinger Bands.

    Parameters:
    data (pd.DataFrame): The input DataFrame containing Bollinger Bands.
    lookback (int): The lookback period to determine the regime.

    Returns:
    pd.Series: A series containing the identified regime for each row.
    """
    price = data['BASKET_MINUS_SYNTHETIC']
    if ewma != 0: 
        price = data['BASKET_MINUS_SYNTHETIC'].ewm(halflife=ewma).mean()
    upper = data['UPPER_BAND']
    lower = data['LOWER_BAND']

    # Create a rolling window of size lookback
    rolling_window = price.rolling(window=lookback)

    # Check if price is above upper band or below lower band
    above_upper = (price >= upper).rolling(window=lookback).sum()
    below_lower = (price <= lower).rolling(window=lookback).sum()

    # Count contiguous touches of upper and lower bands
    touched_upper = (above_upper > 1).astype(int)
    touched_lower = (below_lower > 1).astype(int)

    # Assign regimes based on the touched bands
    regimes = pd.Series(index=data.index, dtype='object')
    regimes.loc[(touched_upper == 1) & (touched_lower == 1)] = 'OSCILLATING'
    regimes.loc[(touched_upper == 1) & (touched_lower == 0)] = 'RIDING_UPPER'
    regimes.loc[(touched_upper == 0) & (touched_lower == 1)] = 'RIDING_LOWER'
    regimes.fillna('NEUTRAL', inplace=True)

    # Fill the initial lookback period with 'NEUTRAL'
    regimes.iloc[:lookback] = 'NEUTRAL'

    return regimes

# Apply the identify_regime function to your DataFrame
df_fairs['REGIME'] = identify_regime(df_fairs, mean=df_fairs['BASKET_MINUS_SYNTHETIC'].mean(), lookback=400, ewma=5)

In [54]:
def generate_signals(data, mean_price):
    """
    Generate trading signals based on the identified regimes and Bollinger Bands.

    Parameters:
    data (pd.DataFrame): The input DataFrame containing Bollinger Bands and regimes.
    mean_price (float): The mean price to compare against when entering riding regimes.

    Returns:
    pd.Series: A series containing the generated trading signals for each row.
    """
    price = data['BASKET_MINUS_SYNTHETIC']
    upper = data['UPPER_BAND']
    lower = data['LOWER_BAND']
    regime = data['REGIME']

    signals = pd.Series(index=data.index, dtype=object)

    for i in tqdm(range(1, len(data))):
        if regime[i] == 'OSCILLATING':
            if price[i] >= upper[i] and price[i-1] < upper[i-1]:
                signals[i] = 'SHORT'
            elif i < len(data) - 1 and price[i] >= upper[i] and price[i+1] < upper[i+1]:
                signals[i] = "SHORT"
            elif price[i] <= lower[i] and price[i-1] > lower[i-1]:
                signals[i] = 'LONG'
            elif i < len(data) - 1 and price[i] <= lower[i] and price[i+1] > lower[i+1]:
                signals[i] = 'LONG'
        elif regime[i] == 'NEUTRAL' and regime[i-1] != 'NEUTRAL':
            signals[i] = 'CLEAR'
        elif regime[i] == 'RIDING_UPPER' and regime[i-1] != 'RIDING_UPPER':
            if price[i] > mean_price:
                signals[i] = 'CLEAR'
            else:
                signals[i] = 'LONG'
        elif regime[i] == 'RIDING_LOWER' and regime[i-1] != 'RIDING_LOWER':
            if price[i] < mean_price:
                signals[i] = 'CLEAR'
            else:
                signals[i] = 'SHORT'

    return signals

df_fairs['SIGNAL'] = generate_signals(df_fairs, df_fairs['BASKET_MINUS_SYNTHETIC'].mean())

100%|████████████████████████████████████████████████| 9999/9999 [00:00<00:00, 72101.13it/s]


In [55]:
fig = go.Figure()

# Add the BASKET_MINUS_SYNTHETIC line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['BASKET_MINUS_SYNTHETIC'],
                         mode='lines', name='BASKET_MINUS_SYNTHETIC'))

# Add the Upper Bollinger Band line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['UPPER_BAND'],
                         mode='lines', name='Upper Band', line=dict(color='red')))

# Add the Simple Moving Average (SMA) line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['SMA'],
                         mode='lines', name='SMA', line=dict(color='blue')))

# Add the Lower Bollinger Band line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['LOWER_BAND'],
                         mode='lines', name='Lower Band', line=dict(color='green')))

# Find regime switch points
regime_switch_points = df_fairs[df_fairs['REGIME'] != df_fairs['REGIME'].shift(1)]

# Add vertical lines for regime switches
for _, row in regime_switch_points.iterrows():
    fig.add_shape(type='line',
                  x0=row['timestamp'], y0=df_fairs['BASKET_MINUS_SYNTHETIC'].min(),
                  x1=row['timestamp'], y1=df_fairs['BASKET_MINUS_SYNTHETIC'].max(),
                  line=dict(color='black', width=1, dash='dash'))
    
    # Add hover text for regime switches
    fig.add_trace(go.Scatter(x=[row['timestamp']], y=[df_fairs.loc[row.name, 'BASKET_MINUS_SYNTHETIC']],
                             mode='markers', marker=dict(size=0), hoverinfo='text',
                             text=f"Regime: {row['REGIME']}<br>Last Sell Signal: {row['SIGNAL']}"))

# Update the layout
fig.update_layout(title='Bollinger Bands with Regime Switches',
                  xaxis_title='Timestamp',
                  yaxis_title='BASKET_MINUS_SYNTHETIC')

# Display the plot
fig.show()

## backtest

In [30]:
df_fairs['SIGNAL'].value_counts()

SIGNAL
LONG     179
SHORT    169
CLEAR     12
Name: count, dtype: int64

In [31]:
def update_position(signals):
    """
    Update the position based on the last non-nan signal.
    
    Parameters:
    signals (pd.Series): The series containing the trading signals.
    
    Returns:
    pd.Series: A series containing the updated positions.
    """
    last_signal = None
    positions = []
    
    for signal in signals:
        if pd.notna(signal):
            last_signal = signal
        
        if last_signal == 'LONG':
            position = 60
        elif last_signal == 'SHORT':
            position = -60
        else:
            position = 0
        
        positions.append(position)
    
    return pd.Series(positions, index=signals.index)

# Update the position based on the trading signals
df_fairs['POSITION'] = update_position(df_fairs['SIGNAL'])

In [32]:
# Initialize the "CASH" column with zeros
df_fairs['CASH'] = 0

# Calculate the position differences
df_fairs['POSITION_DIFF'] = df_fairs['POSITION'].diff().fillna(0)

# Update the "CASH" column based on position changes
df_fairs['CASH'] = -df_fairs['POSITION_DIFF'] * df_fairs['BASKET_MINUS_SYNTHETIC']

# Calculate the cumulative cash
df_fairs['CUMULATIVE_CASH'] = df_fairs['CASH'].cumsum()

df_fairs['PNL'] = df_fairs['CUMULATIVE_CASH'] + df_fairs['POSITION'] * df_fairs["BASKET_MINUS_SYNTHETIC"]

In [33]:
df_fairs[df_fairs['POSITION_DIFF'] != 0]

timestamp    CHOCOLATE  STRAWBERRIES         ROSES  GIFT_BASKET  \
300      30000  8036.000000   3998.306202  14885.000000      71392.5   
586      58600  8033.666667   3988.000000  14761.500000      71198.5   
693      69300  8031.500000   3987.000000  14764.500000      71292.5   
853      85300  8025.698113   3983.000000  14721.750000      71105.5   
993      99300  8029.327044   3995.000000  14787.500000      71228.5   
1055    105500  8029.500000   3998.500000  14768.000000      71273.5   
1219    121900  8028.000000   4001.713262  14729.000000      71277.5   
1278    127800  8037.741117   3998.319865  14749.000000      71300.0   
1395    139500  8043.000000   4001.000000  14759.500000      71400.5   
1596    159600  8041.296875   3992.500000  14800.000000      71455.5   
1770    177000  8026.000000   3995.806020  14733.761364      71239.0   
1897    189700  8024.500000   4002.500000  14746.714286      71380.5   
1952    195200  8016.658228   4002.181159  14758.500000      71263.5   
2201    220100  7991.250000   4002.267409  14739.500000      71106.5   
2716    271600  7999.000000   4001.000000  14779.500000      71052.5   
2871    287100  7996.000000   3994.500000  14731.500000      70886.5   
2989    298900  8005.000000   3986.000000  14720.000000      70915.5   
3079    307900  8018.500000   3988.287234  14714.691489      70918.5   
3129    312900  8016.000000   3989.202797  14733.000000      71003.5   
3391    339100  8015.325444   4009.000000  14800.500000      71257.5   
3505    350500  8010.335484   4010.000000  14784.500000      71308.5   
3562    356200  8002.000000   4014.745342  14742.747368      71160.5   
3741    374100  8030.000000   4017.237885  14759.500000      71351.5   
3964    396400  8016.500000   4015.000000  14746.000000      71209.5   
4044    404400  8022.276382   4012.310105  14744.000000      71144.0   
4350    435000  8040.500000   4018.500000  14723.500000      71237.5   
4430    443000  8038.000000   4014.283401  14711.744186      71252.5   
5234    523400  7999.282209   4043.000000  14727.734043      71496.5   
5325    532500  8011.292994   4046.785479  14718.257426      71476.5   
5495    549500  8011.000000   4039.226361  14667.807692      71466.5   
5603    560300  8022.285714   4042.801980  14685.790698      71479.5   
5739    573900  8025.275000   4044.775362  14689.500000      71546.5   
5938    593800  8008.000000   4040.500000  14705.000000      71425.5   
6149    614900  8000.259067   4038.500000  14730.288889      71401.5   
6559    655900  7993.742331   4045.740984  14618.687500      71255.5   
6905    690500  7999.348066   4043.000000  14577.730337      71207.5   
7116    711600  8002.763441   4035.000000  14560.700000      71124.5   
7151    715100  8010.682927   4037.500000  14558.273585      71222.5   
7285    728500  8023.500000   4035.000000  14472.284091      71103.0   
7398    739800  8035.681081   4034.206790  14425.500000      71170.5   
7498    749800  8045.316092   4032.728814  14436.000000      71158.5   
7565    756500  8053.500000   4034.987531  14431.715909      71272.5   
7732    773200  8048.000000   4029.000000  14435.297297      71161.5   
7833    783300  8037.279793   4020.500000  14433.724138      71127.5   
7978    797800  8030.000000   4021.000000  14494.217949      71091.5   
8205    820500  8022.000000   4021.000000  14551.500000      71036.5   
8276    827600  8032.316384   4021.000000  14591.500000      71160.5   
8439    843900  8037.648352   4023.495781  14571.000000      71218.5   
8798    879800  8038.500000   4012.768559  14485.000000      70911.5   
8891    889100  8040.500000   4012.751381  14446.500000      70980.5   
9123    912300  8024.500000   4021.031469  14402.712871      71122.5   
9241    924100  8015.242105   4025.714286  14426.000000      71011.5   
9406    940600  8021.331551   4027.807339  14463.768116      71007.5   
9510    951000  8018.500000   4033.500000  14458.000000      71093.5   
9635    963500  8012.296053   4035.800643  14

In [34]:
df_fairs['POSITION'].value_counts()

POSITION
-60    4238
 60    3916
 0     1846
Name: count, dtype: int64

In [35]:
import plotly.graph_objects as go

# Create the plot
fig = go.Figure()

# Add the CUMULATIVE_CASH line
fig.add_trace(go.Scatter(x=df_fairs['timestamp'], y=df_fairs['PNL'],
                         mode='lines', name='Cum'))

# Update the layout
fig.update_layout(title='Cumulative Cash Over Time',
                  xaxis_title='Timestamp',
                  yaxis_title='Cumulative Cash')

# Display the plot
fig.show()

# gridsearch

In [36]:
import itertools

def run_backtest(data, bb_window, bb_std, lookback):
    # Calculate Bollinger Bands
    data = bollinger_bands(data, window=bb_window, num_std=bb_std)

    # Identify the regime
    data['REGIME'] = identify_regime(data, mean=data['BASKET_MINUS_SYNTHETIC'].mean(), lookback=lookback)

    # Generate trading signals
    mean_price = data['BASKET_MINUS_SYNTHETIC'].mean()
    data['SIGNAL'] = generate_signals(data, mean_price)

    # Update the position based on the trading signals
    data['POSITION'] = update_position(data['SIGNAL'])

    # Initialize the "CASH" column with zeros
    data['CASH'] = 0

    # Calculate the position differences
    data['POSITION_DIFF'] = data['POSITION'].diff().fillna(0)

    # Update the "CASH" column based on position changes
    data['CASH'] = -data['POSITION_DIFF'] * data['BASKET_MINUS_SYNTHETIC']

    # Calculate the cumulative cash
    data['CUMULATIVE_CASH'] = data['CASH'].cumsum()

    # Calculate the PNL
    data['PNL'] = data['CUMULATIVE_CASH'] + data['POSITION'] * data["BASKET_MINUS_SYNTHETIC"]

    return data

# Define the arrays of candidate values for each parameter
bb_windows = [ 75, 100, 150, 200, 250, 300, 350, 400, 500]
bb_stds = [1.5,1.75, 2,2.25, 2.5]
lookbacks = [50,75,100, 125, 150, 175, 200]

# Perform the grid search
results = []
for bb_window, bb_std, lookback in itertools.product(bb_windows, bb_stds, lookbacks):
    # Run the backtest with the current parameter values
    data = run_backtest(df_fairs.copy(), bb_window, bb_std, lookback)

    # Get the final PNL
    final_pnl = data['PNL'].iloc[-1]

    # Store the results
    results.append({
        'bb_window': bb_window,
        'bb_std': bb_std,
        'lookback': lookback,
        'pnl': final_pnl
    })

    # Print the parameters and PNL for each iteration
    print(f"Bollinger Bands Window: {bb_window}, Bollinger Bands Std: {bb_std}, Lookback: {lookback}, PNL: {final_pnl}")

# Find the best parameters based on the highest PNL
best_result = max(results, key=lambda x: x['pnl'])
print("\nBest Parameters:")
print(f"Bollinger Bands Window: {best_result['bb_window']}")
print(f"Bollinger Bands Std: {best_result['bb_std']}")
print(f"Lookback: {best_result['lookback']}")
print(f"PNL: {best_result['pnl']}")

100%|███████████████████████████████████████████████| 9999/9999 [00:00<00:00, 100125.21it/s]


Bollinger Bands Window: 75, Bollinger Bands Std: 1.5, Lookback: 50, PNL: 44237.009883513674


100%|███████████████████████████████████████████████| 9999/9999 [00:00<00:00, 112538.26it/s]


Bollinger Bands Window: 75, Bollinger Bands Std: 1.5, Lookback: 75, PNL: 31066.521696601412


100%|████████████████████████████████████████████████| 9999/9999 [00:00<00:00, 93497.46it/s]


...

Bollinger Bands Window: 500, Bollinger Bands Std: 2.5, Lookback: 150, PNL: 13168.65304341627


100%|███████████████████████████████████████████████| 9999/9999 [00:00<00:00, 159341.51it/s]


Bollinger Bands Window: 500, Bollinger Bands Std: 2.5, Lookback: 175, PNL: 13997.594290631823


100%|███████████████████████████████████████████████| 9999/9999 [00:00<00:00, 155343.44it/s]

Bollinger Bands Window: 500, Bollinger Bands Std: 2.5, Lookback: 200, PNL: 12742.780857096368

Best Parameters:
Bollinger Bands Window: 200
Bollinger Bands Std: 1.75
Lookback: 175
PNL: 48120.84648591466
